# Proyecto Integrado 2
---

### 1. Objetivo del proyecto 

Una empresa emergente vende productos alimenticios. Se debe investigar el comportamiento del usuario para la aplicación de la empresa.

---


### 2. Carga de dataset y procesamiento de datos 


In [43]:
# Importación de librerías neceserarias
import pandas as pd
import seaborn as sns
from matplotlib import pyplot as plt
from plotly import graph_objects as go
import plotly.express as px
import re
from datetime import time
import numpy as np
from scipy.stats import ttest_ind
import scipy.stats as stats

In [44]:
#Asignación de variable al dataset

def load_data():
    try:
        # Intentar cargar los datos de la forma local
        logs = pd.read_csv('logs_exp_us.csv', sep='\t') # Reemplaza con la ruta local real
        return logs
    except FileNotFoundError:
        # Si la carga local falla, intentar la carga desde la instancia de revisión
        try:
            logs = pd.read_csv('/datasets/logs_exp_us.csv', sep='\t')
            return logs
        except FileNotFoundError:
            print("No se pudo encontrar el archivo en ninguna de las ubicaciones.")
            return None

# Llamar a la función para cargar los datos
logs = load_data()

In [45]:
#Visualización de la información del dataset
logs.info()
logs.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244126 entries, 0 to 244125
Data columns (total 4 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   EventName       244126 non-null  object
 1   DeviceIDHash    244126 non-null  int64 
 2   EventTimestamp  244126 non-null  int64 
 3   ExpId           244126 non-null  int64 
dtypes: int64(3), object(1)
memory usage: 7.5+ MB


EventName         DeviceIDHash  EventTimestamp  ExpId
0         MainScreenAppear  4575588528974610257      1564029816    246
1         MainScreenAppear  7416695313311560658      1564053102    246
2  PaymentScreenSuccessful  3518123091307005509      1564054127    248
3         CartScreenAppear  3518123091307005509      1564054127    248
4  PaymentScreenSuccessful  6217807653094995999      1564055322    248

In [46]:
#Cambiar el nombre de las columnas 
new_names = {'EventName': 'Event_Name',
            'DeviceIDHash': 'User_ID',
            'EventTimestamp': 'Event_Timestamp',
            'ExpId': 'Exp_Id'}

# Renombrar columnas usando el diccionario 
logs = logs.rename(columns=new_names)

logs.columns

Index(['Event_Name', 'User_ID', 'Event_Timestamp', 'Exp_Id'], dtype='object')

In [47]:
#Búsqueda de valores ausentes 
logs.isna().sum()

Event_Name         0
User_ID            0
Event_Timestamp    0
Exp_Id             0
dtype: int64

In [48]:
#Búsqueda de filas duplicadas 
logs.duplicated().sum()

np.int64(413)

In [49]:
#Eliminación de filas duplicadas
logs.drop_duplicates().reset_index(inplace= True)
logs

Event_Name              User_ID  Event_Timestamp  Exp_Id
0              MainScreenAppear  4575588528974610257       1564029816     246
1              MainScreenAppear  7416695313311560658       1564053102     246
2       PaymentScreenSuccessful  3518123091307005509       1564054127     248
3              CartScreenAppear  3518123091307005509       1564054127     248
4       PaymentScreenSuccessful  6217807653094995999       1564055322     248
...                         ...                  ...              ...     ...
244121         MainScreenAppear  4599628364049201812       1565212345     247
244122         MainScreenAppear  5849806612437486590       1565212439     246
244123         MainScreenAppear  5746969938801999050       1565212483     246
244124         MainScreenAppear  5746969938801999050       1565212498     246
244125       OffersScreenAppear  5746969938801999050       1565212517     246

[244126 rows x 4 columns]

In [50]:
#Agregar columna con fecha 
logs['Event_Timestamp'] = pd.to_datetime(logs['Event_Timestamp'], unit= 's')
logs['Date'] = logs['Event_Timestamp'].values.astype(dtype='datetime64[D]')

logs.head()


Event_Name              User_ID     Event_Timestamp  Exp_Id  \
0         MainScreenAppear  4575588528974610257 2019-07-25 04:43:36     246   
1         MainScreenAppear  7416695313311560658 2019-07-25 11:11:42     246   
2  PaymentScreenSuccessful  3518123091307005509 2019-07-25 11:28:47     248   
3         CartScreenAppear  3518123091307005509 2019-07-25 11:28:47     248   
4  PaymentScreenSuccessful  6217807653094995999 2019-07-25 11:48:42     248   

        Date  
0 2019-07-25  
1 2019-07-25  
2 2019-07-25  
3 2019-07-25  
4 2019-07-25

---
### 3. Estudiar y comprobar los datos

In [51]:
#Número de eventos que hay 
print('Número de eventos:', logs['Event_Name'].count())

#Número de usuarios 
print('Número de usuarios:', logs['User_ID'].nunique())

#Promedio de eventos por usuario
print('Número promedio de eventos por usuario:', logs.groupby('User_ID')['Event_Name'].count().mean())

Número de eventos: 244126
Número de usuarios: 7551
Número promedio de eventos por usuario: 32.33028737915508


In [52]:
#Périodo de tiempo que cubren los datos 
print('Fecha de inicio:', logs['Date'].min())
print('Fecha de finalización:', logs['Date'].max())

#Representación gráfica del pérido de tiempo 
df = px.data.stocks()
fig = px.histogram(logs, x="Event_Timestamp", text_auto='.2s',
            title="Histograma por fecha y hora", 
            color_discrete_sequence=px.colors.sequential.RdBu,
            template='simple_white')
fig.update_layout(bargap=0.2)
fig.show()


Fecha de inicio: 2019-07-25 00:00:00
Fecha de finalización: 2019-08-07 00:00:00


 Los eventos más antiguos podrían terminar en los registros de algunos usuarios o usuarias por razones técnicas y esto podría sesgar el panorama general.

In [53]:
#Périodo de tiempo que representa realmente los datos
new_data= logs[logs['Date'] >= '2019-08-01']
new_data.reset_index(inplace= False)
new_data

Event_Name              User_ID     Event_Timestamp  Exp_Id  \
2828              Tutorial  3737462046622621720 2019-08-01 00:07:28     246   
2829      MainScreenAppear  3737462046622621720 2019-08-01 00:08:00     246   
2830      MainScreenAppear  3737462046622621720 2019-08-01 00:08:55     246   
2831    OffersScreenAppear  3737462046622621720 2019-08-01 00:08:58     246   
2832      MainScreenAppear  1433840883824088890 2019-08-01 00:08:59     247   
...                    ...                  ...                 ...     ...   
244121    MainScreenAppear  4599628364049201812 2019-08-07 21:12:25     247   
244122    MainScreenAppear  5849806612437486590 2019-08-07 21:13:59     246   
244123    MainScreenAppear  5746969938801999050 2019-08-07 21:14:43     246   
244124    MainScreenAppear  5746969938801999050 2019-08-07 21:14:58     246   
244125  OffersScreenAppear  5746969938801999050 2019-08-07 21:15:17     246   

             Date  
2828   2019-08-01  
2829   2019-08-01  
2830   2019-08-01  
2831   2019-08-01  
2832   2019-08-01  
...           ...  
244121 2019-08-07  
244122 2019-08-07  
244123 2019-08-07  
244124 2019-08-07  
244125 2019-08-07  

[241298 rows x 5 columns]

In [54]:
#Perdida de eventos al excluir datos antiguos
event_number= logs.groupby('Event_Name').agg({'User_ID':'count'})
new_event_number= new_data.groupby('Event_Name').agg({'User_ID':'count'})
new_event_number= event_number.merge(new_event_number, on= 'Event_Name')
new_event_number.columns = ['Old', 'New']
new_event_number['Lost'] = new_event_number['Old'] - new_event_number['New']
print(new_event_number) 
print(' ')
print('Número total de eventos antiguos:', new_event_number['Old'].sum())
print('Número total de eventos nuevos:', new_event_number['New'].sum())
print('Número total de eventos perdidos:', new_event_number['Lost'].sum())
print(' ')

                            Old     New  Lost
Event_Name                                   
CartScreenAppear          42731   42365   366
MainScreenAppear         119205  117431  1774
OffersScreenAppear        46825   46350   475
PaymentScreenSuccessful   34313   34113   200
Tutorial                   1052    1039    13
 
Número total de eventos antiguos: 244126
Número total de eventos nuevos: 241298
Número total de eventos perdidos: 2828
 


In [55]:
#Perdida de usuarios al excluir datos antiguos
users_number= logs.groupby('Event_Name').agg({'User_ID':'nunique'})

new_users_number= new_data.groupby('Event_Name').agg({'User_ID':'nunique'})
new_users_number= users_number.merge(new_users_number, on= 'Event_Name')
new_users_number.columns = ['Old', 'New']
new_users_number['Lost'] = new_users_number['Old'] - new_users_number['New']
print(new_users_number) 
print(' ')
print('Número total de usuarios antiguos:', new_users_number['Old'].sum())
print('Número total de usuarios nuevos:', new_users_number['New'].sum())
print('Número total de usuarios perdidos:', new_users_number['Lost'].sum())
print(f"""
Porcentaje de usuarios que permanecen: {100*round(new_data["User_ID"].nunique() / logs["User_ID"].nunique(), 3)}
Porcentaje de usuarios que eliminamos: {100*round(1 - new_data["User_ID"].nunique() / logs["User_ID"].nunique(), 3)}
""")


                          Old   New  Lost
Event_Name                               
CartScreenAppear         3749  3734    15
MainScreenAppear         7439  7419    20
OffersScreenAppear       4613  4593    20
PaymentScreenSuccessful  3547  3539     8
Tutorial                  847   840     7
 
Número total de usuarios antiguos: 20195
Número total de usuarios nuevos: 20125
Número total de usuarios perdidos: 70

Porcentaje de usuarios que permanecen: 99.8
Porcentaje de usuarios que eliminamos: 0.2



In [56]:
#Confirmación de usuarios existentes en los tres grupos experimentales.
groups = new_data.groupby('Exp_Id').agg({'User_ID':'nunique'})
groups


User_ID
Exp_Id         
246        2484
247        2513
248        2537

---
### 4. Embudo de eventos

In [57]:
#Frecuencia en eventos 
event_frequency = new_data['Event_Name'].value_counts().sort_values(ascending=False).reset_index()
event_frequency

Event_Name   count
0         MainScreenAppear  117431
1       OffersScreenAppear   46350
2         CartScreenAppear   42365
3  PaymentScreenSuccessful   34113
4                 Tutorial    1039

In [58]:
#Cantidad de usuarios que realizaron cada evento
users_by_event= new_data.groupby("Event_Name")["User_ID"].nunique().sort_values(ascending=False).reset_index()
users_by_event

Event_Name  User_ID
0         MainScreenAppear     7419
1       OffersScreenAppear     4593
2         CartScreenAppear     3734
3  PaymentScreenSuccessful     3539
4                 Tutorial      840

In [59]:
#Proporción de usuarios
proportion= (new_data.groupby("Event_Name")["User_ID"].nunique()/new_data["User_ID"].nunique()).sort_values(ascending=False).reset_index()
proportion

Event_Name   User_ID
0         MainScreenAppear  0.984736
1       OffersScreenAppear  0.609636
2         CartScreenAppear  0.495620
3  PaymentScreenSuccessful  0.469737
4                 Tutorial  0.111495

In [60]:
#Embudo de eventos
users_by_event["Users_In_Previous_Step"] = users_by_event["User_ID"].shift(1)
users_by_event["Conversion_Rate"] = users_by_event["User_ID"] / \
    users_by_event["Users_In_Previous_Step"]
users_by_event["Dropoff_Rate"] = 1 - users_by_event["Conversion_Rate"]

users_by_event.head()

Event_Name  User_ID  Users_In_Previous_Step  Conversion_Rate  \
0         MainScreenAppear     7419                     NaN              NaN   
1       OffersScreenAppear     4593                  7419.0         0.619086   
2         CartScreenAppear     3734                  4593.0         0.812976   
3  PaymentScreenSuccessful     3539                  3734.0         0.947777   
4                 Tutorial      840                  3539.0         0.237355   

   Dropoff_Rate  
0           NaN  
1      0.380914  
2      0.187024  
3      0.052223  
4      0.762645

Interpretación del Embudo:

1.Alta tasa de abandono inicial: La mayor caída se observa entre la pantalla principal y la pantalla de ofertas. Esto sugiere que muchos usuarios abandonan el proceso en las primeras etapas, posiblemente debido a un diseño poco atractivo, contenido poco relevante o dificultades para encontrar lo que buscan.

2.Mejoría en la conversión: A medida que los usuarios avanzan hacia las etapas finales del embudo, la tasa de conversión aumenta. Esto indica que los elementos de diseño, la propuesta de valor y el proceso de compra son más efectivos en las etapas posteriores.


3.Caída significativa antes del tutorial: Existe una caída considerable en el número de usuarios después de completar el proceso de pago. Esto podría deberse a que el tutorial es opcional o que no se presenta de manera atractiva, haciendo que los usuarios lo eviten.

Recomendaciones:

-Optimizar la página de inicio: Centrarse en mejorar el diseño, el contenido y la experiencia del usuario en la pantalla principal para reducir el abandono inicial.

-Analizar la página de ofertas: Investigar por qué los usuarios abandonan la página de ofertas. Podría ser debido a ofertas poco atractivas, dificultades para encontrar productos o problemas de navegación.

-Promocionar el tutorial: Considerar formas de hacer que el tutorial sea más atractivo y valioso para los usuarios, por ejemplo, ofreciendo incentivos o destacando los beneficios.

-Simplificar el proceso de pago: Asegurarse de que el proceso de pago sea lo más sencillo y seguro posible para reducir el abandono en esta etapa.

-Segmentar a los usuarios: Analizar el comportamiento de diferentes segmentos de usuarios (nuevos vs. recurrentes, dispositivos móviles vs. escritorio) para identificar patrones y adaptar la experiencia del usuario en consecuencia.

---
### 5.Estudiar los resultados del experimento

In [61]:
#Usuarios por grupos 
users_by_group= new_data.groupby("Exp_Id")["User_ID"].nunique().sort_values(ascending=False).reset_index()
users_by_group


Exp_Id  User_ID
0     248     2537
1     247     2513
2     246     2484

---

In [62]:
new_data.head(3)

Event_Name              User_ID     Event_Timestamp  Exp_Id  \
2828          Tutorial  3737462046622621720 2019-08-01 00:07:28     246   
2829  MainScreenAppear  3737462046622621720 2019-08-01 00:08:00     246   
2830  MainScreenAppear  3737462046622621720 2019-08-01 00:08:55     246   

           Date  
2828 2019-08-01  
2829 2019-08-01  
2830 2019-08-01

In [70]:
x_data = new_data.groupby("Exp_Id")["User_ID"].nunique()
x_data

Exp_Id
246    4941
247    2466
248    2537
Name: User_ID, dtype: int64

In [75]:
conversions = new_data[["User_ID", "Exp_Id"]].drop_duplicates()

converted = pd.DataFrame(data={
    "User_ID": new_data[new_data["Event_Name"] == "MainScreenAppear"]["User_ID"].unique(),
    "Converted": 1
})

conversions = conversions.merge(converted, on="User_ID", how="left")
conversions["Converted"] = conversions["Converted"].fillna(0)

conversions

User_ID  Exp_Id  Converted
0     3737462046622621720     246        1.0
1     1433840883824088890     247        1.0
2     4899590676214355127     246        1.0
3     4899590676214355127     247        1.0
4     1182179323890311443     246        1.0
...                   ...     ...        ...
9939  5365227480683749189     248        1.0
9940  6660805781687343085     246        1.0
9941  7823752606740475984     246        1.0
9942  3454683894921357834     247        1.0
9943  3454683894921357834     246        1.0

[9944 rows x 3 columns]

In [66]:
# Datos
group_246= new_data[new_data['Exp_Id']== 246].groupby('Exp_Id', as_index=False).agg({'User_ID' : 'nunique'})
group_247= new_data[new_data['Exp_Id']== 247].groupby('Exp_Id', as_index=False).agg({'User_ID' : 'nunique'})

# Realizar la prueba t
t_statistic, p_value = stats.ttest_ind(group_246, group_247)

# Establecer el nivel de significancia
alpha = 0.05

# Interpretar los resultados
if p_value < alpha:
    print("Existe una diferencia significativa entre los grupos (p-value =", p_value, ")")
else:
    print("No existe una diferencia significativa entre los grupos (p-value =", p_value, ")")


ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [ ]:
import pandas as pd
import scipy.stats as stats

# Suponiendo que tienes un DataFrame llamado 'data' con las columnas de tu imagen

# Crear dataframes para cada grupo
group_246 = data[data['Exp_Id'] == 246]
group_247 = data[data['Exp_Id'] == 247]

# Definir la conversión (ajusta esto según tu definición)
conversion_event = 'ClickedButton'  # Reemplaza con tu evento de conversión

# Crear una nueva columna booleana indicando si ocurrió la conversión
group_246['clicked'] = group_246['Event_Name'] == conversion_event
group_247['clicked'] = group_247['Event_Name'] == conversion_event

# Calcular la tasa de clics en cada grupo
click_rate_246 = group_246['clicked'].mean()
click_rate_247 = group_247['clicked'].mean()

# Crear la tabla de contingencia
contingency_table = [[np.sum(group_246['clicked']), len(group_246) - np.sum(group_246['clicked'])],
                    [np.sum(group_247['clicked']), len(group_247) - np.sum(group_247['clicked'])]]

# Realizar la prueba chi-cuadrado
chi2, p, dof, expected = stats.chi2_contingency(contingency_table)

print("p-value:", p)


Definir la Hipótesis Nula y Alternativa:

Hipótesis Nula (H0): No hay diferencia significativa en la métrica de interés entre los grupos 246 y 247.
Hipótesis Alternativa (H1): Sí hay una diferencia significativa en la métrica de interés entre los grupos 246 y 247.
Seleccionar la Métrica de Interés:

¿Qué quieres comparar? Al igual que en un test A/B, puedes elegir diversas métricas como:
Tasa de clics: Porcentaje de usuarios que hacen clic en un elemento específico.
Tiempo en página: Duración promedio de una visita a una página.
Número de páginas vistas por sesión: Cantidad promedio de páginas vistas por usuario.
Dividir los Datos:

Filtra los datos para obtener dos conjuntos separados: uno para el grupo 246 y otro para el grupo 247.
Seleccionar la Prueba Estadística:

La elección de la prueba dependerá del tipo de datos y de la pregunta que estés tratando de responder. Por ejemplo:
Prueba t: Para comparar medias de dos grupos independientes cuando los datos son normales.
Prueba de Mann-Whitney U: Para comparar medias de dos grupos independientes cuando los datos no son normales.
Prueba chi-cuadrado: Para comparar proporciones entre dos grupos.
Realizar la Prueba y Obtener el Valor p:

Utiliza una herramienta estadística como Python (con librerías como SciPy o Statsmodels) o un software especializado para realizar la prueba y obtener el valor p.
Interpretar el Valor p:

Si p < 0.05: Hay evidencia estadística para rechazar la hipótesis nula. Esto significa que hay una diferencia significativa entre los dos grupos, lo cual es inesperado en un test A/A y podría indicar un problema en el experimento.
Si p >= 0.05: No hay evidencia suficiente para rechazar la hipótesis nula. Esto es lo esperado en un test A/A, indicando que ambos grupos son comparables.